In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from IPython.display import display
import plotly
import plotly.graph_objects as go
from plotly.subplots import make_subplots

pd.set_option("display.max_columns", None)

# 03 plotly.py のさまざまなグラフ

## 3-2 専門的なグラフ

- 統計
  - 箱ひげ図
  - バイオリン図
  - ヒストグラム
  - 2次元ヒストグラム
  - エラーバー
  - 平行（座標）プロット
- 科学
  - ヒートマップ
  - 等高線図
  - ポーラチャート
  - レーダーチャート
  - 鶏頭図
  - 三角図
- 金融
  - ローソク足
  - ウォーターフォール図
  - ファンネル図
- 地理
  - 階級区分図（コロプレスマップ）
  - 地図上の散布図

In [2]:
# サンプルデータの読み込み
tips = plotly.data.tips()
display(tips)

total_bill   tip     sex smoker   day    time  size
0         16.99  1.01  Female     No   Sun  Dinner     2
1         10.34  1.66    Male     No   Sun  Dinner     3
2         21.01  3.50    Male     No   Sun  Dinner     3
3         23.68  3.31    Male     No   Sun  Dinner     2
4         24.59  3.61  Female     No   Sun  Dinner     4
..          ...   ...     ...    ...   ...     ...   ...
239       29.03  5.92    Male     No   Sat  Dinner     3
240       27.18  2.00  Female    Yes   Sat  Dinner     2
241       22.67  2.00    Male    Yes   Sat  Dinner     2
242       17.82  1.75    Male     No   Sat  Dinner     2
243       18.78  3.00  Female     No  Thur  Dinner     2

[244 rows x 7 columns]

### 3.2.1 箱ひげ図 (Box trace)

In [5]:
# Box クラスの引数 y にリストなどのデータを渡す
# 曜日ごとのデータを抽出

tips_by_day = tips.groupby("day")
days = ["Thur", "Fri", "Sat", "Sun"]

box_fig = go.Figure()
for day in days:
    box_fig.add_trace(
        go.Box(
            y=tips_by_day.get_group(day)["tip"],
            name=day
        )
    )

box_fig.show()

### 3.2.2 バイオリン図 (Violin trace)

In [7]:
# Violin クラスの引数 y にリストなどのデータを渡す

violin_fig = make_subplots(rows=1, cols=2)

# 1列目のサププロット
# 箱ひげ図を重ねて描画
for day in days:
    violin_fig.add_trace(
        go.Violin(
            y=tips_by_day.get_group(day)["tip"],
            name=day,
            box_visible=True,
        ),
        row=1,
        col=1,
    )
# 2列目のサププロット
# smoker 列のデータを左右に分けて描画
for day in days:
    df = tips_by_day.get_group(day)
    # smoker 列をデータで分類
    smoker = df.loc[df["smoker"] == "Yes"]
    non_smoker = df.loc[df["smoker"] == "No"]

    violin_fig.add_trace(
        go.Violin(
            x=smoker["day"],
            y=smoker["tip"],
            side="negative",  # 左側に描画
            name=f"{day}: smoker",
        ),
        row=1,
        col=2,
    )
    violin_fig.add_trace(
        go.Violin(
            x=non_smoker["day"],
            y=non_smoker["tip"],
            side="positive",  # 右側に描画
            name=f"{day}: non-smoker",
        ),
        row=1,
        col=2,
    )

violin_fig.show()

### 3.2.2 ヒストグラム (Histogram trace)

In [8]:
np.random.seed(1)
data0 = np.random.normal(10, 1, 10_000)
data1 = np.random.normal(12, 1.5, 10_000)

histogram_fig = make_subplots(rows=1, cols=2)

histogram_fig.add_trace(go.Histogram(x=data0, name="data0"), row=1, col=1)
histogram_fig.add_trace(go.Histogram(x=data1, name="data1"), row=1, col=1)

# 横向きに描画
histogram_fig.add_trace(go.Histogram(y=data0, name="data0"), row=1, col=2)
histogram_fig.add_trace(
    go.Histogram(
        y=data1,
        name="data1",
        nbinsy=50,  # ビンの数を変更
    ),
    row=1,
    col=2
)

histogram_fig.show()

In [9]:
# ヒストグラムを積み上げる
# Layout クラスの引数 barmode="stack"

go.Figure(
    [go.Histogram(x=data0, name="data0"), go.Histogram(x=data1, name="data1")],
    layout=go.Layout(barmode="stack"),
).show()

- Histogram クラスの引数 histnorm
  - percent: 合計を 100 とした相対度数（百分率）
  - probability: 合計すると 1 とした相対度数
  - density: 密度推定
  - probability density: 合計値を 1 とした密度推定

In [11]:
# 累積ヒストグラム
# trace の cumulative.enabled 属性を True に設定する

probability_cumulative_histogram_fig = make_subplots(rows=1, cols=2)

probability_cumulative_histogram_fig.add_trace(
    go.Histogram(
        x=data0,
        histnorm="probability",
        name="probability"
    ),
    row=1,
    col=1,
)
probability_cumulative_histogram_fig.add_trace(
    go.Histogram(
        x=data0,
        cumulative={"enabled": True},
        name="cumulative"
    ),
    row=1,
    col=2,
)

probability_cumulative_histogram_fig.show()

In [18]:
# ヒストグラムの範囲を指定する
# trace の xbins 属性を設定する
# start: 開始位置
# end: 終了位置
# size: 階級の幅

go.Figure(go.Histogram(
    x=data0,
    xbins=dict(
        start=8,
        end=11,
        size=0.01
    ),
)).show()

### 3.2.4 2次元ヒストグラム (Histogram2d trace)

- 2次元ヒストグラム
  - 2変数を2次元の座標に取り、2変数の値の組み合わせの頻度をカラースケールで表現する

In [24]:
histogram2d_fig = make_subplots(rows=1, cols=2)

# 2次元ヒストグラム
histogram2d_fig.add_trace(
    go.Histogram2d(x=data0, y=data1),
    row=1,
    col=1
)
# 等高線
histogram2d_fig.add_trace(
    go.Histogram2dContour(x=data0, y=data1, showscale=False),
    row=1,
    col=2
)
histogram2d_fig.update_layout(coloraxis_showscale=False)

histogram2d_fig.show()

### 3.2.5 エラーバー

- trace の error_x 属性または error_y 属性に設定する
  - type
    - percent: エラー値を割合で指定
    - constant: エラー値を定数で指定
    - sqrt: 値の平方根がエラー値となる
    - data: 各要素のエラー値を指定
  - symmetric
    - True: 対称なエラーバー
    - False： 非対称なエラーバー
  - array: 各要素のエラー値を指定
  - arrayminus: エラーバーを非対称 (symmetric=False) した場合、各要素の負の値を指定
  - value: エラー値を指定
  - valueminus: エラーバーを非対称 (symmetric=False) した場合、エラー値の負の値を指定

In [29]:
np.random.seed(1)
x = np.arange(1, 4)
y = np.random.rand(3)
err_values = np.random.rand(3) * 0.1
err_values_minus = np.random.rand(3) * 0.1

error_fig = make_subplots(rows=2, cols=2)

# Y値のエラーバーを一定の値で指定した
# 折れ線グラフ
error_fig.add_trace(
    go.Scatter(
        x=x,
        y=y,
        error_x=dict(
            type="constant",
            value=0.1
        ),
    ),
    row=1,
    col=1,
)
# 各要素ごとにX値のエラーバーを指定した
# 折れ線グラフ
error_fig.add_trace(
    go.Scatter(
        x=x,
        y=y,
        error_x=dict(
            type="data",
            array=err_values
        ),
    ),
    row=1,
    col=2,
)
# Y値のエラーバーを正の値と負の値をそれぞれ指定した
# 棒グラフ
error_fig.add_trace(
    go.Bar(
        x=x,
        y=y,
        error_y=dict(
            symmetric=False,
            type="data",
            array=err_values,
            arrayminus=err_values_minus,
        ),
    ),
    row=2,
    col=1,
)

error_fig.show()

### 3.2.6 平行座標プロット (Parcoords trace)

- Parcoords クラスの引数 dimensions に描画するデータを複数格納したリストを渡す
  - label: 要素名を指定（軸ラベルとして表示される）
  - values: リストなどの値を指定
  - 軸間の線分を色分けするには、引数 line に "color" をキーとして、リストなどのデータを値とした辞書を渡す

In [30]:
# データ取得
iris = plotly.data.iris()
display(iris)

sepal_length  sepal_width  petal_length  petal_width    species  \
0             5.1          3.5           1.4          0.2     setosa   
1             4.9          3.0           1.4          0.2     setosa   
2             4.7          3.2           1.3          0.2     setosa   
3             4.6          3.1           1.5          0.2     setosa   
4             5.0          3.6           1.4          0.2     setosa   
..            ...          ...           ...          ...        ...   
145           6.7          3.0           5.2          2.3  virginica   
146           6.3          2.5           5.0          1.9  virginica   
147           6.5          3.0           5.2          2.0  virginica   
148           6.2          3.4           5.4          2.3  virginica   
149           5.9          3.0           5.1          1.8  virginica   

     species_id  
0             1  
1             1  
2             1  
3             1  
4             1  
..          ...  
145           3  
146           3  
147           3  
148           3  
149           3  

[150 rows x 6 columns]

In [32]:
# species_id 列で要素を色分けする

go.Figure(
    [
        go.Parcoords(
            dimensions=[
                dict(label="sepal_length", values=iris["sepal_length"]),
                dict(label="sepal_width", values=iris["sepal_width"]),
                dict(label="petal_length", values=iris["petal_length"]),
                dict(label="petal_width", values=iris["petal_width"]),
            ],
            line=dict(color=iris["species_id"]),
        )
    ]
).show()

### 3.2.7 平行プロット (Parcats trace)

In [ ]:
# サンプルデータの読み込み
tips = plotly.data.tips()
display(tips)

In [33]:
go.Figure(
    [
        go.Parcats(
            dimensions=[
                dict(label="sex", values=tips["sex"]),
                dict(label="smoker", values=tips["smoker"]),
                dict(label="day", values=tips["day"]),
                dict(label="time", values=tips["time"]),
            ],
            line=dict(color=tips["size"]),
        )
    ]
).show()

### 3.2.8 ヒートマップ (Heatmap trace)

In [35]:
np.random.seed(1)

x = np.arange(0, 5)
y = np.arange(0, 50, 10)
z = np.random.randn(5, 5)

In [34]:
go.Figure([go.Heatmap(x=x, y=y, z=z)]).show()

### 3.2.9 等高線図 (Contour trace)

In [36]:
go.Figure([go.Contour(x=x, y=y, z=z)]).show()

### 3.2.10 ポーラチャート (Scatterpolar trace)

- ポーラーチャート描画する方法
  - Scatterpolar trace
  - BarPolar trace
    - r: 極座標の原点からの距離を渡す
    - theta: 角度を角度法で渡す（離散値の場合、等間隔に割り当てられる）

In [42]:
np.random.seed(7)

r1 = np.random.rand(6)
theta = np.linspace(0, 360, 7)[: -1]
r1_close = np.hstack([r1, np.array(r1[0])])
r2 = r1 + np.random.uniform(-0.3, 0.3, 6)
r2_close = np.hstack([r2, np.array(r2[0])])

label = list("abcdefa")

polar_fig = make_subplots(
    rows=2,
    cols=2,
    specs=[
        [dict(type="polar"), dict(type="polar")],
        [dict(type="polar"), dict(type="polar")],
    ],
)

# 点で描画（散布図）
polar_fig.add_trace(
    go.Scatterpolar(
        r=r1, theta=theta, mode="markers"
    ),
    row=1,
    col=1,
)

# 線で描画（レーダーチャート）
polar_fig.add_trace(
    go.Scatterpolar(
        r=r1_close, theta=label, mode="lines", fill="toself", name="r1"
    ),
    row=1,
    col=2,
)
polar_fig.add_trace(
    go.Scatterpolar(
        r=r2_close, theta=label, mode="lines", fill="toself", name="r2"
    ),
    row=1,
    col=2,
)

# 積み上げて描画（鶏頭図）
polar_fig.add_trace(
    go.Barpolar(
        r=r1, theta=label
    ),
    row=2,
    col=1,
)
polar_fig.add_trace(
    go.Barpolar(
        r=r2, theta=label
    ),
    row=2,
    col=1,
)

polar_fig.show()

### 3.2.11 三角図 (Scatterternary trace)

In [43]:
# データセットの読み込み
election = plotly.data.election()
display(election)

district  Coderre  Bergeron  \
0                                  101-Bois-de-Liesse     2481      1829   
1                               102-Cap-Saint-Jacques     2525      1163   
2                                11-Sault-au-Récollet     3348      2770   
3                                        111-Mile-End     1734      4782   
4                                      112-DeLorimier     1770      5933   
5                                    113-Jeanne-Mance     1455      3599   
6                                    12-Saint-Sulpice     3252      2521   
7                          121-La Pointe-aux-Prairies     5456      1760   
8                             122-Pointe-aux-Trembles     4734      1879   
9                            123-Rivière-des-Prairies     5737       958   
10                                        13-Ahuntsic     2979      3430   
11                                  131-Saint-Édouard     1827      6408   
12                             132-Étienne-Desmarteau     2331      5748   
13                                 133-Vieux-Rosemont     2670      4962   
14                                 134-Marie-Victorin     3673      3155   
15                           14-Bordeaux-Cartierville     3612      1554   
16                                 141-Côte-de-Liesse     4308      1320   
17                                 142-Norman-McLaren     4104      1459   
18                              151-Saint-Léonard-Est     3931       882   
19                            152-Saint-Léonard-Ouest     5387      1184   
20  161-Saint-HenriPetite-BourgognePointe-Saint-Ch...     2432      3368   
21                                162-Saint-PaulÉmard     2566      2092   
22                      171-ChamplainL'Île-des-Soeurs     3347      2562   
23                           172-Desmarchais-Crawford     2476      2631   
24                                   181-Peter-McGill     1451       754   
25                                  182-Saint-Jacques     1906      2169   
26                                   183-Sainte-Marie     1347      2827   
27                                   191-Saint-Michel     3668       984   
28                              192-François-Perrault     2878      2666   
29                                       193-Villeray     2201      5819   
30                                 194-Parc-Extension     2420      1793   
31                                           21-Ouest     2184       691   
32                                             22-Est     1589       708   
33                                          23-Centre     2526       851   
34                                      31-Darlington     1873      1182   
35                                 32-Côte-des-Neiges     1644      1950   
36                                         33-Snowdon     1548      1503   
37                             34-Notre-Dame-de-Grâce     1773      2653   
38                                          35-Loyola     2040      1437   
39                                        41-du Canal     1165       832   
40                                42-J.-Émery-Provost     1193       653   
41                                    43-Fort-Rolland     1325      1205   
42                               51-Sault-Saint-Louis     4201      1642   
43                                 52-Cecil-P.-Newman     3536      1330   
44                                 61-Pierre-Foretier      631       258   
45                            62-Denis-Benjamin-Viger      595       226   
46                                  63-Jacques-Bizard      518       224   
47                                64-Sainte-Geneviève      332       131   
48                                  71-Tétreaultville     3694      2589   
49                        72-MaisonneuveLongue-Pointe     2746      3250   
50                                       73-Hochelaga     1546      3679   
51                                      74-Louis-Riel     3509      2178   
52               

In [44]:
scatterternary_trace = go.Scatterternary(
    a=election["Bergeron"],
    b=election["Coderre"],
    c=election["Joly"],
    mode="markers",
    marker=dict(size=election["total"] * 1e-3),
)
scatterternary_layout = go.Layout(
    ternary=dict(
        aaxis=dict(title="Bergeron"),
        baxis=dict(title="Coderre"),
        caxis=dict(title="Joly"),
    )
)

go.Figure(scatterternary_trace, scatterternary_layout).show()

### 3.2.12 ローソク足 (Candlestick trace)

In [45]:
stocks = plotly.data.stocks(indexed=True)
stocks.index = pd.to_datetime(stocks.index)
display(stocks)

company         GOOG      AAPL      AMZN        FB      NFLX      MSFT
date                                                                  
2018-01-01  1.000000  1.000000  1.000000  1.000000  1.000000  1.000000
2018-01-08  1.018172  1.011943  1.061881  0.959968  1.053526  1.015988
2018-01-15  1.032008  1.019771  1.053240  0.970243  1.049860  1.020524
2018-01-22  1.066783  0.980057  1.140676  1.016858  1.307681  1.066561
2018-01-29  1.008773  0.917143  1.163374  1.018357  1.273537  1.040708
...              ...       ...       ...       ...       ...       ...
2019-12-02  1.216280  1.546914  1.425061  1.075997  1.463641  1.720717
2019-12-09  1.222821  1.572286  1.432660  1.038855  1.421496  1.752239
2019-12-16  1.224418  1.596800  1.453455  1.104094  1.604362  1.784896
2019-12-23  1.226504  1.656000  1.521226  1.113728  1.567170  1.802472
2019-12-30  1.213014  1.678000  1.503360  1.098475  1.540883  1.788185

[105 rows x 6 columns]

In [46]:
# 1か月ごとにリサンプリング
# 四本値にリサンプリング

ohlc_df = (
    stocks["GOOG"]
    .resample("1M")
    .ohlc()
)
display(ohlc_df)

open      high       low     close
date                                              
2018-01-31  1.000000  1.066783  1.000000  1.008773
2018-02-28  0.941528  1.022282  0.941528  0.978852
2018-03-31  1.052448  1.052448  0.926821  0.936093
2018-04-30  0.913639  0.973445  0.913639  0.950990
2018-05-31  0.996398  1.015668  0.967457  1.015668
2018-06-30  1.016911  1.048311  1.012175  1.012175
2018-07-31  1.034421  1.123631  1.034421  1.110213
2018-08-31  1.122824  1.122824  1.089573  1.105205
2018-09-30  1.056794  1.082778  1.056794  1.082778
2018-10-31  1.050008  1.050008  0.959682  0.959682
2018-11-30  0.967266  0.992924  0.928917  0.992924
2018-12-31  0.940439  0.971403  0.888689  0.971403
2019-01-31  0.959137  1.007730  0.959137  1.007730
2019-02-28  0.993495  1.035165  0.993495  1.035165
2019-03-31  1.036372  1.093692  1.036372  1.064488
2019-04-30  1.095189  1.154187  1.075456  1.075456
2019-05-31  1.056286  1.056286  1.001270  1.001270
2019-06-30  0.967167  1.017828  0.967167  0.980657
2019-07-31  1.026637  1.134437  1.025285  1.083249
2019-08-31  1.077824  1.077906  1.044510  1.077906
2019-09-30  1.093175  1.124593  1.093175  1.096867
2019-10-31  1.102719  1.155603  1.102719  1.155603
2019-11-30  1.189743  1.211063  1.175199  1.183927
2019-12-31  1.216280  1.226504  1.213014  1.213014

In [47]:
go.Figure(
    [
        go.Candlestick(
            x=ohlc_df.index,
            open=ohlc_df["open"],
            high=ohlc_df["high"],
            low=ohlc_df["low"],
            close=ohlc_df["close"],
        )
    ]
).show()

### 3.2.13 ウォーターフォール図 (Waterfall trace)

- ウォーターフォール図
  - 初期値・累計値・値の増減を長方形の長さで表現する
  - 値が増加した場合は前の値が底辺になり、値が減少した場合は値が上辺となる
  - 初期値と累計値は 0 が底辺となる（値が正の場合）
  - 引数 measure:
    - relative: 相対値
    - total: 合計値

In [48]:
# 損益計算書のデータをウォーターフォール図に描画

go.Figure(
    go.Waterfall(
        x=[
            "売上高",
            "売上原価",
            "売上総利益",
            "販売比及び一般管理費",
            "営業利益",
            "営業外収益",
            "営業外費用",
            "経常利益",
            "特別利益",
            "特別損失",
            "税引前当期純利益",
            "法人税等",
            "当期純利益",
        ],
        measure=[
            "relative",
            "relative",
            "total",
            "relative",
            "total",
            "relative",
            "relative",
            "total",
            "relative",
            "relative",
            "total",
            "relative",
            "total",
        ],
        y=[1000, -300, 0, -150, 0, 100, -80, 0, 3, -5, 0, -100, 0]
    )
).show()

### 3.2.14 ファンネル図 (Funnel trace)

- ファンネル図
  - 値が絞り込まれる様子を漏斗（ろうと・じょうご）の形でひょうげんする
  - 値は図形（長方形）の長さで表現され、次の要素は初期値からの変化または前の値の変化から描画される
  - x: 各段階の値
  - y: 各段階のラベル
  - textinfo: 要素の「表示形式」と「基準値」をスペースで連結した文字列を指定する
    - 表示形式（複数指定する場合は `+` で連結した文字列を指定する）
      - label: ラベル
      - percent: 変化率
    - 基準値（百分率を表示する場合の基準となる値）
      - initial: 初期値
      - previous: 前の値
      - total: 合計値

In [49]:
funnel_fig = go.Figure()

funnel_fig.add_trace(
    go.Funnel(
        name="商品 A",
        y=["閲覧", "クリック", "カートに追加", "購入"],
        x=[300, 150, 20, 18],
        textinfo="percent initial",
    )
)
funnel_fig.add_trace(
    go.Funnel(
        name="商品 B",
        y=["閲覧", "クリック", "カートに追加", "購入"],
        x=[200, 40, 15, 13],
        textinfo="label+percent previous",
    )
)

funnel_fig.show()

### 3.2.15 階級区分図 (Choropleth trace)

- Choropleth クラス
  - locations: locationmode に従った地域データ
  - locationmode: 地域データの定義を文字列で指定
  - z: 地域ごとの値となるリストなどのデータ

In [50]:
# データセットの読み込み
gapminder = plotly.data.gapminder()
gapminder_2007 = gapminder.loc[gapminder["year"] == 2007]
display(gapminder_2007)

country continent  year  lifeExp       pop     gdpPercap  \
11           Afghanistan      Asia  2007   43.828  31889923    974.580338   
23               Albania    Europe  2007   76.423   3600523   5937.029526   
35               Algeria    Africa  2007   72.301  33333216   6223.367465   
47                Angola    Africa  2007   42.731  12420476   4797.231267   
59             Argentina  Americas  2007   75.320  40301927  12779.379640   
...                  ...       ...   ...      ...       ...           ...   
1655             Vietnam      Asia  2007   74.249  85262356   2441.576404   
1667  West Bank and Gaza      Asia  2007   73.422   4018332   3025.349798   
1679         Yemen, Rep.      Asia  2007   62.698  22211743   2280.769906   
1691              Zambia    Africa  2007   42.384  11746035   1271.211593   
1703            Zimbabwe    Africa  2007   43.487  12311143    469.709298   

     iso_alpha  iso_num  
11         AFG        4  
23         ALB        8  
35         DZA       12  
47         AGO       24  
59         ARG       32  
...        ...      ...  
1655       VNM      704  
1667       PSE      275  
1679       YEM      887  
1691       ZMB      894  
1703       ZWE      716  

[142 rows x 8 columns]

In [52]:
go.Figure(
    [
        go.Choropleth(
            locations=gapminder_2007["country"],
            locationmode="country names",  # 位置データを国名で指定
            z=gapminder_2007["lifeExp"],
        )
    ]
).show()

### 3.2.16 地図上の散布図 (Scattergeo trace)

- Scattergeo クラス
  - lon: 経度
  - lat: 緯度
  - mode: "markers"
  - marker: Scatter クラスと同様の設定ができる

In [53]:
populations = np.array([38_505_000, 34_365_000, 28_125_000])
area = np.array([8_223, 3_367, 2_240])
lon, lat = [139.691711, 106.845131, 77.216667], [35.6, -6.214620, 28.666668]
text = ["Tokyo", "Jakarta", "Delhi"]

go.Figure(
    [
        go.Scattergeo(
            lon=lon,
            lat=lat,
            marker=dict(
                size=populations / 1_000_000,     # 要素の大きさ
                color=populations / area,         # 要素の色
                cmin=1000,                        # 色の下限値
                cmax=15000,                       # 色の上限値
                colorbar=dict(title= "人口密度"),  # カラーバーを表示、タイトルを指定
            ),
            text=text,       # ホバーツールに表示するテキスト
            mode="markers",  # 散布図として描画
        )
    ],
    layout=dict(geo=dict(scope="asia"))
).show()

### 3.2.17 地図上の折れ線グラフ (Scattergeo trace)

In [55]:
go.Figure(
    go.Scattergeo(
        lon=lon + [-74.005966],
        lat=lat + [40.714272],
        mode="lines",
        text=text,
    ),
    layout=dict(
        geo=dict(projection=dict(type="azimuthal equal area"))
    ),
).show()

### 3.2.18 mapbox の利用

- [mapbox](https://www.mapbox.com/)
- [mapbox jp](https://www.mapbox.jp/)